In [4]:
import csv

# Open the CSV file
with open('C:\\Users\\alexb\\StravaConcat1', 'r', encoding="utf8") as file:
    # Create a CSV reader object
    csv_reader = csv.reader(file)
    
    # Get the header row and remove the first element
    headers = next(csv_reader)[1:]
    print(headers)
    
    # Create a dictionary to hold the data
    data_dict = {}
    results = []
    
    # Iterate through each row and append the values to the corresponding column list
    for row in csv_reader:
        name = row[0]
        # print(row[1])
        # Create a new list for the name if it doesn't exist in the dictionary
        if name not in data_dict:
            data_dict[name] = [[] for _ in range(len(headers))]
        
        for i, value in enumerate(row[1:]):
            data_dict[name][i].append(value)
    
    # Print the values for each name and column
    for name, columns in data_dict.items():
        # print(f"Name: {name}")
        print(columns)
        for i, column in enumerate(columns):
            if all(elem=='' for elem in column):
                continue
            if all(elem=='—' for elem in column):
                continue
            results.append({'Name': name, 'attributes': {headers[i]: column}})


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [5]:


# final = {'Name':'Attributes'}
final = {}

for i,dict in enumerate(results):
    attributes = dict['attributes']['Lap']
    dictionary_string = attributes[0]  # Access the first element of the list (the dictionary as a string)
    attributes = eval(dictionary_string)  # Evaluate the string to convert it into a dictionary
    name = dict['Name']

    output_list = []
    lap_list = []
    pace_input = []
    GAP_input = []
    Time_input = []
    Elev_input = []
    bpm_input = []

    input_list = attributes['Distance']
    input_list_copy = attributes['Distance']
    input_list = [float(item.replace(' mi', '')) for item in input_list]
    print(f'input list is {input_list}')

    print(f'name is {name}')
    print(f'attributes are {attributes}')

    #DISTANCE
    if 'Distance' in attributes.keys():
        print('Distance is a key')
        attributes['Distance'] = [s.strip(' mi') for s in attributes['Distance']]
        attributes['Distance'] = [eval(p) for p in attributes['Distance']]
        original_key = attributes['Distance'][:]
        print(original_key)

    def update_distance():
        remainder = 0
        for i, x in enumerate(original_key):
            # Add the remainder to the current value
            x += remainder

            # Calculate the number of 1's and the new remainder
            num_ones = int(x)
            remainder = x - num_ones

            # Add the 1's to the output list
            output_list.extend([1] * num_ones)

        output_list.append(remainder)
        attributes['Distance'] = output_list
        print(f'Distance total is {output_list}')

    update_distance()

    print(f'input_list after DISTANCE is {input_list}')
    print(f'input_list_copy after DISTANCE is {input_list_copy}')

    #LAP
    if 'Lap' in attributes.keys():
        print(len(output_list))
        for y in range(len(output_list)):
            lap_list.append(y+1)

        attributes['Lap'] = lap_list
        print(attributes['Lap'])
        print(f'lap list is {lap_list}')    

    #PACE
    if 'Pace' in attributes.keys() and '—' not in attributes['Pace']:
        attributes['Pace'] = [s.strip(' /mi') for s in attributes['Pace']]
        def convert_time_to_seconds(time_str_list):
            for time_str in time_str_list:
                if ':' in time_str:
                    time_parts = time_str.split(':')
                    if len(time_parts) == 2: # If there are two colons, assume format is mm:ss
                        minutes, seconds = time_parts
                        pace_input.append(int(minutes) * 60 + int(seconds))
                    elif len(time_parts) == 3: # If there are three colons, assume format is hh:mm:ss
                        hours, minutes, seconds = time_parts
                        pace_input.append(int(hours) * 3600 + int(minutes) * 60 + int(seconds))
                else:
                    time_str = eval(time_str)
                    pace_input.append(time_str)
            return pace_input
        attributes['Pace'] = convert_time_to_seconds(attributes['Pace'])
        pace_input = attributes['Pace']
        print(f'pace input is {pace_input}')
        #PACE RESULT
        pace_result = []
        print(f'length input list is {len(input_list)}')
        print(f'input list is {input_list}')
        for i, x in enumerate(input_list):
            if x == None:
                print('None reached again')
                continue
            print(f'{input_list} iterated through {i} times')
            print(f'result is {pace_result}')
            integer, remain = divmod(x, 1)
            pace_result.extend([pace_input[i]] * int(integer))
            if remain > 0:
                print(f'{input_list_copy[i]} {i} index remainder is {remain}')
                if i+2 < (len(input_list)):
                    print(f'length of input list is {len(input_list)}')
                    if (remain) + input_list[i+1] > 1:
                        pace = remain * pace_input[i] + (1 - remain) * pace_input[i+1]
                        pace_result.append(pace)
                        print(f'current pace_result is = {pace_result}')
                        input_list[i+1] += (remain-1)
                        print(f'speed is {pace}m/s from distance {input_list[i]}')
                        print("")
                        print("")


                    elif ((remain) + input_list[i+1] + input_list[i+2]) > 1 and i+2 < len(input_list):
                        pace = remain * pace_input[i] + pace_input[i+1] * input_list[i+1] + (1 - remain - input_list[i+1]) * pace_input[i+2]
                        input_list[i+2] += (remain + input_list[i+1]-1)
                        print(f'speed is {pace}m/s from distance {input_list[i]}')
                        pace_result.append(pace)
                        print(f'current pace_result is = {pace_result}')
                        input_list[i+1]=None
                        print('None reached')
                        print("")
                        print("")


                    elif i+3 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] > 1:
                        pace = remain*pace_input[i] + pace_input[i+1]*input_list[i+1] + input_list[i+2]*pace_input[i+2] + (1-remain-input_list[i+1]-input_list[i+2])*pace_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        print(f'None reached part two')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        pace_result.append(pace)

                    elif i+4 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] + input_list[i+4] > 1:
                        pace = remain*pace_input[i] + pace_input[i+1]*input_list[i+1] + input_list[i+2]*pace_input[i+2] + input_list[i+3]*pace_input[i+3] + (1-remain-input_list[i+1]-input_list[i+2]-input_list[i+3])*pace_input[i+4]
                        input_list[i+4] += (-1+remain+input_list[i+1]+input_list[i+2]+input_list[i+3])
                        print(f'None reached part three')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        pace_result.append(pace)

                    elif remain + input_list[i+1] + input_list[i+2] < 1:
                        pace = remain * pace_input[i] + input_list[i+1]*pace_input[i+1]+input_list[i+2]*pace_input[i+2]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        pace_result.append(pace)
                        print(f'current pace_result is = {pace_result}')
                        
                    elif i+3<len(input_list) and remain + input_list[i+1] + input_list[i+2] + input_list[i+3] < 1:
                        pace = remain * pace_input[i] + input_list[i+1]*pace_input[i+1]+input_list[i+2]*pace_input[i+2]+input_list[i+3]*pace_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        pace_result.append(pace)
                        print(f'current pace_result is = {pace_result}')
                        
                    elif i+4<len(input_list) and remain + input_list[i+1] + input_list[i+2] +input_list[i+3] + input_list[i+4] < 1:
                        pace = remain * pace_input[i] + input_list[i+1]*pace_input[i+1]+input_list[i+2]*pace_input[i+2]+input_list[i+3]*pace_input[i+3]+input_list[i+4]*pace_input[i+4]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        input_list[i+4]=None
                        pace_result.append(pace)
                        print(f'current pace_result is = {pace_result}')
                        
                        

                        
                elif i+1 < (len(input_list)):        
                    if remain + input_list[i+1] > 1:
                        print(f'1st elif satisfied')
                        pace = remain*pace_input[i]+(1-remain)*pace_input[i+1]
                        pace_result.append(pace)
                        input_list[i+1]+=(remain-1)
                        print(f'current pace_result is {pace_result}')
                        
                        
                    elif remain + input_list[i+1] < 1:
                        print(f'2nd elif satisfied')
                        pace = remain*pace_input[i]+input_list[i+1]*pace_input[i+1]
                        input_list[i+1]=None
                        pace_result.append(pace)

                elif i+2 >= (len(input_list)):
                    print(f'3rd elif satisfied')
                    pace_result.append(pace_input[i])

                else:
                    print('No Conditions Satisfied')



        print("")
        print("")
        print(f'FINAL pace_result IS {pace_result}')
    attributes['Pace'] = pace_result
    input_list = original_key[:]
    input_list_copy = original_key[:]
    print(f'input_list after PACE is {input_list}')
    print(f'input_list_copy after PACE is {input_list_copy}')


    #GAP
    if 'GAP' in attributes.keys() and '—' not in attributes['GAP']:
        attributes['GAP'] = [s.strip(' /mi') for s in attributes['GAP']]
        def convert_time_to_seconds(time_str_list):
            for time_str in time_str_list:
                if ':' in time_str:
                    time_parts = time_str.split(':')
                    if len(time_parts) == 2: # If there are two colons, assume format is mm:ss
                        minutes, seconds = time_parts
                        GAP_input.append(int(minutes) * 60 + int(seconds))
                    elif len(time_parts) == 3: # If there are three colons, assume format is hh:mm:ss
                        hours, minutes, seconds = time_parts
                        GAP_input.append(int(hours) * 3600 + int(minutes) * 60 + int(seconds))
                else:
                    time_str = eval(time_str)
                    GAP_input.append(time_str)
            return GAP_input
        attributes['GAP'] = convert_time_to_seconds(attributes['GAP'])
        GAP_input = attributes['GAP']
        print(f'GAP input is {GAP_input}')
        #GAP RESULT
        GAP_result = []
        print(f'length input list is {len(input_list)}')
        print(f'input list is {input_list}')
        for i, x in enumerate(input_list):
            if x == None:
                print('None reached again')
                continue
            print(f'{input_list} iterated through {i} times')
            print(f'result is {GAP_result}')
            integer, remain = divmod(x, 1)
            GAP_result.extend([GAP_input[i]] * int(integer))
            if remain > 0:
                print(f'{input_list_copy[i]} {i} index remainder is {remain}')
                if i+2 < (len(input_list)):
                    print(f'length of input list is {len(input_list)}')
                    if (remain) + input_list[i+1] > 1:
                        GAP = remain * GAP_input[i] + (1 - remain) * GAP_input[i+1]
                        GAP_result.append(GAP)
                        print(f'current GAP_result is = {GAP_result}')
                        input_list[i+1] += (remain-1)
                        print(f'speed is {GAP}m/s from distance {input_list[i]}')
                        print("")
                        print("")


                    elif ((remain) + input_list[i+1] + input_list[i+2]) > 1 and i+2 < len(input_list):
                        GAP = remain * GAP_input[i] + GAP_input[i+1] * input_list[i+1] + (1 - remain - input_list[i+1]) * GAP_input[i+2]
                        input_list[i+2] += (remain + input_list[i+1]-1)
                        print(f'speed is {GAP}m/s from distance {input_list[i]}')
                        GAP_result.append(GAP)
                        print(f'current GAP_result is = {GAP_result}')
                        input_list[i+1]=None
                        print('None reached')
                        print("")
                        print("")


                    elif i+3 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] > 1:
                        GAP = remain*GAP_input[i] + GAP_input[i+1]*input_list[i+1] + input_list[i+2]*GAP_input[i+2] + (1-remain-input_list[i+1]-input_list[i+2])*GAP_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        print(f'None reached part two')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        GAP_result.append(GAP)

                    elif i+4 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] + input_list[i+4] > 1:
                        GAP = remain*GAP_input[i] + GAP_input[i+1]*input_list[i+1] + input_list[i+2]*GAP_input[i+2] + input_list[i+3]*GAP_input[i+3] + (1-remain-input_list[i+1]-input_list[i+2]-input_list[i+3])*GAP_input[i+4]
                        input_list[i+4] += (-1+remain+input_list[i+1]+input_list[i+2]+input_list[i+3])
                        print(f'None reached part three')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        GAP_result.append(GAP)

                    elif remain + input_list[i+1] + input_list[i+2] < 1:
                        GAP = remain * GAP_input[i] + input_list[i+1]*GAP_input[i+1]+input_list[i+2]*GAP_input[i+2]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        GAP_result.append(GAP)
                        print(f'current GAP_result is = {GAP_result}')
                        
                    elif i+3<len(input_list) and remain + input_list[i+1] + input_list[i+2] + input_list[i+3] < 1:
                        GAP = remain * GAP_input[i] + input_list[i+1]*GAP_input[i+1]+input_list[i+2]*GAP_input[i+2]+input_list[i+3]*GAP_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        GAP_result.append(GAP)
                        print(f'current GAP_result is = {GAP_result}')
                        
                    elif i+4<len(input_list) and remain + input_list[i+1] + input_list[i+2] +input_list[i+3] + input_list[i+4] < 1:
                        GAP = remain * GAP_input[i] + input_list[i+1]*GAP_input[i+1]+input_list[i+2]*GAP_input[i+2]+input_list[i+3]*GAP_input[i+3]+input_list[i+4]*GAP_input[i+4]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        input_list[i+4]=None
                        GAP_result.append(GAP)
                        print(f'current GAP_result is = {GAP_result}')
                        
                        

                        
                elif i+1 < (len(input_list)):        
                    if remain + input_list[i+1] > 1:
                        print(f'1st elif satisfied')
                        GAP = remain*GAP_input[i]+(1-remain)*GAP_input[i+1]
                        GAP_result.append(GAP)
                        input_list[i+1]+=(remain-1)
                        print(f'current GAP_result is {GAP_result}')
                        
                        
                    elif remain + input_list[i+1] < 1:
                        print(f'2nd elif satisfied')
                        GAP = remain*GAP_input[i]+input_list[i+1]*GAP_input[i+1]
                        input_list[i+1]=None
                        GAP_result.append(GAP)

                elif i+2 >= (len(input_list)):
                    print(f'3rd elif satisfied')
                    GAP_result.append(GAP_input[i])

                else:
                    print('No Conditions Satisfied')



        print("")
        print("")
        print(f'FINAL GAP_result IS {GAP_result}')
    attributes['GAP'] = GAP_result
    input_list = original_key[:]
    input_list_copy = original_key[:]
    print(f'input_list after GAP is {input_list}')
    print(f'input_list_copy after GAP is {input_list_copy}')

    #Elev
    if 'Elev' in attributes.keys() and 'null ft' not in attributes['Elev']:
        attributes['Elev'] = [s.strip(' ft') for s in attributes['Elev']]
        attributes['Elev'] = [eval(p) for p in attributes['Elev']]
        Elev_input = attributes['Elev']
        print(f'Elev input is {Elev_input}')
        #Elev RESULT
        Elev_result = []
        print(f'length input list is {len(input_list)}')
        print(f'input list is {input_list}')
        for i, x in enumerate(input_list):
            if x == None:
                print('None reached again')
                continue
            print(f'{input_list} iterated through {i} times')
            print(f'result is {Elev_result}')
            integer, remain = divmod(x, 1)
            Elev_result.extend([Elev_input[i]] * int(integer))
            if remain > 0:
                print(f'{input_list_copy[i]} {i} index remainder is {remain}')
                if i+2 < (len(input_list)):
                    print(f'length of input list is {len(input_list)}')
                    if (remain) + input_list[i+1] > 1:
                        Elev = remain * Elev_input[i] + (1 - remain) * Elev_input[i+1]
                        Elev_result.append(Elev)
                        print(f'current Elev_result is = {Elev_result}')
                        input_list[i+1] += (remain-1)
                        print(f'speed is {Elev}m/s from distance {input_list[i]}')
                        print("")
                        print("")


                    elif ((remain) + input_list[i+1] + input_list[i+2]) > 1 and i+2 < len(input_list):
                        Elev = remain * Elev_input[i] + Elev_input[i+1] * input_list[i+1] + (1 - remain - input_list[i+1]) * Elev_input[i+2]
                        input_list[i+2] += (remain + input_list[i+1]-1)
                        print(f'speed is {Elev}m/s from distance {input_list[i]}')
                        Elev_result.append(Elev)
                        print(f'current Elev_result is = {Elev_result}')
                        input_list[i+1]=None
                        print('None reached')
                        print("")
                        print("")


                    elif i+3 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] > 1:
                        Elev = remain*Elev_input[i] + Elev_input[i+1]*input_list[i+1] + input_list[i+2]*Elev_input[i+2] + (1-remain-input_list[i+1]-input_list[i+2])*Elev_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        print(f'None reached part two')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        Elev_result.append(Elev)

                    elif i+4 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] + input_list[i+4] > 1:
                        Elev = remain*Elev_input[i] + Elev_input[i+1]*input_list[i+1] + input_list[i+2]*Elev_input[i+2] + input_list[i+3]*Elev_input[i+3] + (1-remain-input_list[i+1]-input_list[i+2]-input_list[i+3])*Elev_input[i+4]
                        input_list[i+4] += (-1+remain+input_list[i+1]+input_list[i+2]+input_list[i+3])
                        print(f'None reached part three')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        Elev_result.append(Elev)

                    elif remain + input_list[i+1] + input_list[i+2] < 1:
                        Elev = remain * Elev_input[i] + input_list[i+1]*Elev_input[i+1]+input_list[i+2]*Elev_input[i+2]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        Elev_result.append(Elev)
                        print(f'current Elev_result is = {Elev_result}')
                        
                    elif i+3<len(input_list) and remain + input_list[i+1] + input_list[i+2] + input_list[i+3] < 1:
                        Elev = remain * Elev_input[i] + input_list[i+1]*Elev_input[i+1]+input_list[i+2]*Elev_input[i+2]+input_list[i+3]*Elev_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        Elev_result.append(Elev)
                        print(f'current Elev_result is = {Elev_result}')
                        
                    elif i+4<len(input_list) and remain + input_list[i+1] + input_list[i+2] +input_list[i+3] + input_list[i+4] < 1:
                        Elev = remain * Elev_input[i] + input_list[i+1]*Elev_input[i+1]+input_list[i+2]*Elev_input[i+2]+input_list[i+3]*Elev_input[i+3]+input_list[i+4]*Elev_input[i+4]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        input_list[i+4]=None
                        Elev_result.append(Elev)
                        print(f'current Elev_result is = {Elev_result}')
                        
                        

                        
                elif i+1 < (len(input_list)):        
                    if remain + input_list[i+1] > 1:
                        print(f'1st elif satisfied')
                        Elev = remain*Elev_input[i]+(1-remain)*Elev_input[i+1]
                        Elev_result.append(Elev)
                        input_list[i+1]+=(remain-1)
                        print(f'current Elev_result is {Elev_result}')
                        
                        
                    elif remain + input_list[i+1] < 1:
                        print(f'2nd elif satisfied')
                        Elev = remain*Elev_input[i]+input_list[i+1]*Elev_input[i+1]
                        input_list[i+1]=None
                        Elev_result.append(Elev)

                elif i+2 >= (len(input_list)):
                    print(f'3rd elif satisfied')
                    Elev_result.append(Elev_input[i])

                else:
                    print('No Conditions Satisfied')


        print("")
        print("")
        print(f'FINAL Elev_result IS {Elev_result}')
    attributes['Elev'] = Elev_result
    input_list = original_key[:]
    input_list_copy = original_key[:]
    print(f'input_list after Elev is {input_list}')
    print(f'input_list_copy after Elev is {input_list_copy}')


    #bpm
    if 'HR' in attributes.keys() and '—' not in attributes['HR'] and len(input_list) == len(attributes['HR']):
        attributes['HR'] = [s.strip(' bpm') for s in attributes['HR']]
        attributes['HR'] = [eval(p) for p in attributes['HR']]
        bpm_input = attributes['HR']
        print(f'HR input is {bpm_input}')
        #bpm RESULT
        bpm_result = []
        print(f'length input list is {len(input_list)}')
        print(f'input list is {input_list}')
        for i, x in enumerate(input_list):
            if x == None:
                print('None reached again')
                continue
            print(f'{input_list} iterated through {i} times')
            print(f'result is {bpm_result}')
            integer, remain = divmod(x, 1)
            bpm_result.extend([bpm_input[i]] * int(integer))
            if remain > 0:
                print(f'{input_list_copy[i]} {i} index remainder is {remain}')
                if i+2 < (len(input_list)):
                    print(f'length of input list is {len(input_list)}')
                    if (remain) + input_list[i+1] > 1:
                        bpm = remain * bpm_input[i] + (1 - remain) * bpm_input[i+1]
                        bpm_result.append(bpm)
                        print(f'current bpm_result is = {bpm_result}')
                        input_list[i+1] += (remain-1)
                        print(f'speed is {bpm}m/s from distance {input_list[i]}')
                        print("")
                        print("")


                    elif ((remain) + input_list[i+1] + input_list[i+2]) > 1 and i+2 < len(input_list):
                        bpm = remain * bpm_input[i] + bpm_input[i+1] * input_list[i+1] + (1 - remain - input_list[i+1]) * bpm_input[i+2]
                        input_list[i+2] += (remain + input_list[i+1]-1)
                        print(f'speed is {bpm}m/s from distance {input_list[i]}')
                        bpm_result.append(bpm)
                        print(f'current bpm_result is = {bpm_result}')
                        input_list[i+1]=None
                        print('None reached')
                        print("")
                        print("")


                    elif i+3 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] > 1:
                        bpm = remain*bpm_input[i] + bpm_input[i+1]*input_list[i+1] + input_list[i+2]*bpm_input[i+2] + (1-remain-input_list[i+1]-input_list[i+2])*bpm_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        print(f'None reached part two')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        bpm_result.append(bpm)

                    elif i+4 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] + input_list[i+4] > 1:
                        bpm = remain*bpm_input[i] + bpm_input[i+1]*input_list[i+1] + input_list[i+2]*bpm_input[i+2] + input_list[i+3]*bpm_input[i+3] + (1-remain-input_list[i+1]-input_list[i+2]-input_list[i+3])*bpm_input[i+4]
                        input_list[i+4] += (-1+remain+input_list[i+1]+input_list[i+2]+input_list[i+3])
                        print(f'None reached part three')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        bpm_result.append(bpm)

                    elif remain + input_list[i+1] + input_list[i+2] < 1:
                        bpm = remain * bpm_input[i] + input_list[i+1]*bpm_input[i+1]+input_list[i+2]*bpm_input[i+2]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        bpm_result.append(bpm)
                        print(f'current bpm_result is = {bpm_result}')
                        
                    elif i+3<len(input_list) and remain + input_list[i+1] + input_list[i+2] + input_list[i+3] < 1:
                        bpm = remain * bpm_input[i] + input_list[i+1]*bpm_input[i+1]+input_list[i+2]*bpm_input[i+2]+input_list[i+3]*bpm_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        bpm_result.append(bpm)
                        print(f'current bpm_result is = {bpm_result}')
                        
                    elif i+4<len(input_list) and remain + input_list[i+1] + input_list[i+2] +input_list[i+3] + input_list[i+4] < 1:
                        bpm = remain * bpm_input[i] + input_list[i+1]*bpm_input[i+1]+input_list[i+2]*bpm_input[i+2]+input_list[i+3]*bpm_input[i+3]+input_list[i+4]*bpm_input[i+4]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        input_list[i+4]=None
                        bpm_result.append(bpm)
                        print(f'current bpm_result is = {bpm_result}')
                        

                        
                elif i+1 < (len(input_list)):        
                    if remain + input_list[i+1] > 1:
                        print(f'1st elif satisfied')
                        bpm = remain*bpm_input[i]+(1-remain)*bpm_input[i+1]
                        bpm_result.append(bpm)
                        input_list[i+1]+=(remain-1)
                        print(f'current bpm_result is {bpm_result}')
                        
                        
                    elif remain + input_list[i+1] < 1:
                        print(f'2nd elif satisfied')
                        bpm = remain*bpm_input[i]+input_list[i+1]*bpm_input[i+1]
                        input_list[i+1]=None
                        bpm_result.append(bpm)

                elif i+2 >= (len(input_list)):
                    print(f'3rd elif satisfied')
                    bpm_result.append(bpm_input[i])

                else:
                    print('No Conditions Satisfied')



        print("")
        print("")
        print(f'FINAL bpm_result IS {bpm_result}')
    attributes['HR'] = bpm_result
    input_list = original_key[:]
    input_list_copy = original_key[:]
    print(f'input_list after bpm is {input_list}')
    print(f'input_list_copy after bpm is {input_list_copy}')


    #Time
    if 'Time' in attributes.keys() and '—' not in attributes['Time']:
        def convert_time_to_seconds(time_str_list):
            for time_str in time_str_list:
                if ':' in time_str:
                    time_parts = time_str.split(':')
                    if len(time_parts) == 2: # If there are two colons, assume format is mm:ss
                        minutes, seconds = time_parts
                        Time_input.append(int(minutes) * 60 + int(seconds))
                    elif len(time_parts) == 3: # If there are three colons, assume format is hh:mm:ss
                        hours, minutes, seconds = time_parts
                        Time_input.append(int(hours) * 3600 + int(minutes) * 60 + int(seconds))
                else:
                    time_str = time_str.strip('s')
                    time_str = eval(time_str)
                    Time_input.append(time_str)
            return Time_input
        attributes['Time'] = convert_time_to_seconds(attributes['Time'])
        Time_input = attributes['Time']
        #Time RESULT
        Time_result = []
        for i, x in enumerate(input_list):
            if x == None:
                print('None reached again')
                continue
            print(f'{input_list} iterated through {i} times')
            print(f'result is {Time_result}')
            integer, remain = divmod(x, 1)
            Time_result.extend([Time_input[i]] * int(integer))  
            if remain > 0:
                print(f'{input_list_copy[i]} {i} index remainder is {remain}')
                if i+2 < (len(input_list)):
                    print(f'length of input list is {len(input_list)}')
                    if remain + input_list[i+1] >= 1:
                        print('1st')
                        print(f'first {Time_input[i]}')
                        print(f'second {Time_input[i+1]}')
                        print(f'input + 1 is {input_list[i+1]}')
                        print(1-remain)
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i]) + Time_input[i+1]/(input_list[i+1]/(1-remain))
                        Time_result.append(Time)
                        print(f'current Time_result is = {Time_result}')
                        input_list[i+1] += (remain-1)
                        print(f'speed is {Time}from {i}')
                        print("")
                        print("")


                    elif ((remain) + input_list[i+1] + input_list[i+2]) >= 1 and i+2 < len(input_list):
                        print('2nd')
                        print(Time_input[i]/((input_list_copy[i])/(input_list[i])))
                        print(Time_input[i])
                        print(input_list_copy[i])
                        print(remain)
                        Time = Time_input[i]/(input_list_copy[i]/remain) + Time_input[i+1] + Time_input[i+2]/(input_list_copy[i+2]/(1-(remain+input_list[i+1])))
                        input_list[i+2] += (remain + input_list[i+1]-1)
                        print(f'speed is {Time}m/s from distance {input_list[i]}')
                        Time_result.append(Time)
                        print(f'current Time_result is = {Time_result}')
                        input_list[i+1]=None
                        print('None reached')
                        print("")
                        print("")


                    elif i+3 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] >= 1:
                        print('third')
                        Time = Time_input[i]/((input_list_copy[i])/(remain)) + Time_input[i+1] + Time_input[i+2] + Time_input[i+3]/(input_list_copy[i+3]/(1-(remain+input_list[i+1]+input_list[i+2])))
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        print(f'None reached part two')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        Time_result.append(Time)

                    elif i+4 < len(input_list) and (remain) + input_list[i+1] + input_list[i+2] + input_list[i+3] + input_list[i+4] > 1:
                        
                        Time = Time_input[i]/((input_list_copy[i])/(remain)) + Time_input[i+1] + Time_input[i+2] + Time_input[i+3] + Time_input[i+4]/(input_list_copy[i+4]/(1-(remain+input_list[i+1]+input_list[i+2] + input_list[i+3])))
                        input_list[i+4] += (-1+remain+input_list[i+1]+input_list[i+2]+input_list[i+3])
                        print(f'None reached part three')
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        Time_result.append(Time)

                    elif remain + input_list[i+1] + input_list[i+2] < 1:
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i]) +Time_input[i+1]+Time_input[i+2]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        Time_result.append(Time)
                        print(f'current Time_result is = {Time_result}')

                    elif i+3<len(input_list) and remain + input_list[i+1] + input_list[i+2] + input_list[i+3] < 1:
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i]) +Time_input[i+1]+Time_input[i+2]+Time_input[i+3]
                        input_list[i+3] += (-1+remain+input_list[i+1]+input_list[i+2])
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        Time_result.append(Time)
                        print(f'current Time_result is = {Time_result}')

                    elif i+4<len(input_list) and remain + input_list[i+1] + input_list[i+2] +input_list[i+3] + input_list[i+4] < 1:
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i]) + Time_input[i+1]+Time_input[i+2]+Time_input[i+3]+Time_input[i+4]
                        input_list[i+1]=None
                        input_list[i+2]=None
                        input_list[i+3]=None
                        input_list[i+4]=None
                        Time_result.append(Time)
                        print(f'current Time_result is = {Time_result}')
                        

                elif i+1 < (len(input_list)):        
                    if remain + input_list[i+1] > 1:
                        print(f'1st elif satisfied')
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i])+Time_input[i+1]/(input_list[i+1]/(1-remain))
                        Time_result.append(Time)
                        input_list[i+1]+=(remain-1)
                        print(f'current Time_result is {Time_result}')


                    elif remain + input_list[i+1] < 1:
                        print(remain + input_list[i+1])
                        print(f'2nd elif satisfied')
                        Time = Time_input[i]/(input_list_copy[i]/input_list[i])+Time_input[i+1]
                        input_list[i+1]=None
                        Time_result.append(Time)

                elif i+2 >= (len(input_list)):
                    print(f'3rd elif satisfied')
                    Time = (Time_input[-1]/input_list_copy[-1]) * remain
                    Time_result.append(Time)

                else:
                    print('No Conditions Satisfied')



        print("")
        print("")
        print(f'FINAL Time_result IS {Time_result}')
    attributes['Time'] = Time_result
    input_list = original_key[:]
    input_list_copy = original_key[:]
    print(f'input_list after Time is {input_list}')
    print(f'input_list_copy after Time is {input_list_copy}')


    final[name]=attributes
    

input list is [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.09]
name is Jack Rowe
attributes are {'Lap': ['  1', '  2', '  3', '  4', '  5', '  6', '  7', '  8', '  9', ' 10', ' 11'], 'Distance': ['1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '1.00 mi', '0.09 mi'], 'Time': ['4:58', '4:50', '4:45', '4:47', '4:28', '4:34', '4:34', '4:39', '4:52', '4:26', '22s'], 'Pace': ['4:58 /mi', '4:50 /mi', '4:45 /mi', '4:47 /mi', '4:28 /mi', '4:34 /mi', '4:34 /mi', '4:39 /mi', '4:52 /mi', '4:26 /mi', '3:52 /mi'], 'Elev': ['26 ft', '9 ft', '-1 ft', '-9 ft', '-3 ft', '-8 ft', '-11 ft', '-3 ft', '16 ft', '3 ft', '0 ft'], 'HR': ['126 bpm', '150 bpm', '172 bpm', '172 bpm', '181 bpm', '182 bpm', '183 bpm', '180 bpm', '182 bpm', '184 bpm', '188 bpm']}
Distance is a key
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.09]
Distance total is [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0.09]
input_list after DISTANCE is [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



HR input is [168, 177, 179, 176, 175, 177, 175, 176, 178, 179, 184]
length input list is 11
input list is [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 0 times
result is []
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 1 times
result is [168]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 2 times
result is [168, 177]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 3 times
result is [168, 177, 179]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 4 times
result is [168, 177, 179, 176]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 5 times
result is [168, 177, 179, 176, 175]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 6 times
result is [168, 177, 179, 176, 175, 177]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.1] iterated through 7 times
result

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




11
[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
lap list is [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
pace input is [591, 587, 603, 601, 586, 575, 589, 588, 581, 560, 529]
length input list is 11
input list is [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 0 times
result is []
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 1 times
result is [591]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 2 times
result is [591, 587]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 3 times
result is [591, 587, 603]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 4 times
result is [591, 587, 603, 601]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 5 times
result is [591, 587, 603, 601, 586]
[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.12] iterated through 6 times
result is [591, 587, 603, 601,

HR input is [149, 157, 155, 157, 156, 158, 159, 159, 160, 160, 160, 160, 161, 162, 162, 162, 171]
length input list is 17
input list is [0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.19]
[0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.19] iterated through 0 times
result is []
0.62 0 index remainder is 0.62
length of input list is 17
current bpm_result is = [152.04]
speed is 152.04m/s from distance 0.62


[0.62, 0.24, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.19] iterated through 1 times
result is [152.04]
0.62 1 index remainder is 0.24
length of input list is 17
speed is 155.76m/s from distance 0.24
current bpm_result is = [152.04, 155.76]
None reached


None reached again
[0.62, 0.24, None, 0.48, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.62, 0.19] iterated through 3 times
result is [152.04, 155.76]
0.62 3 index rem

In [6]:
final

{'Jack Rowe': {'Lap': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11],
  'Distance': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0.09],
  'Time': [298, 290, 285, 287, 268, 274, 274, 279, 292, 266, 22.0],
  'Pace': [298, 290, 285, 287, 268, 274, 274, 279, 292, 266, 232],
  'Elev': [26, 9, -1, -9, -3, -8, -11, -3, 16, 3, 0],
  'HR': [126, 150, 172, 172, 181, 182, 183, 180, 182, 184, 188],
  'GAP': [588, 590, 588, 575, 580, 593, 597, 602, 599, 617, 531]},
 'Andy Vernon': {'Lap': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11],
  'Distance': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0.05],
  'Time': [287, 291, 278, 290, 295, 292, 301, 298, 289, 279, 15.0],
  'Pace': [287, 291, 278, 290, 295, 292, 301, 298, 289, 279, 263],
  'Elev': [5, 5, -5, 2, -5, -3, 1, 1, -2, 4, 0],
  'GAP': [588, 590, 588, 575, 580, 593, 597, 602, 599, 617, 531],
  'HR': [126, 150, 172, 172, 181, 182, 183, 180, 182, 184, 188]},
 'Joshua Grace': {'Lap': [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11],
  'Distance': [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0.05],
  'Time': [281, 282, 287,